In [1]:
// #load "NbHelper.fsx"

#I "../../../Vide.Common/src/Vide.Common/bin/Debug/netstandard2.0"
#r "Vide.Common.dll"

#r "nuget: Plotly.NET, 4.2.0"
#r "nuget: Plotly.NET.Interactive, 4.2.0"

Installed Packages Plotly.NET, 4.2.0 Plotly.NET.Interactive, 4.2.0

Loading extensions from `C:\Users\ronal\.nuget\packages\plotly.net.interactive\4.2.0\interactive-extensions\dotnet\Plotly.NET.Interactive.dll`

In [2]:
open Vide
open Vide.Dsp
open Vide.Dsp.Operators
open Vide.Dsp.DiscreteTime

open Plotly.NET
open Plotly.NET.LayoutObjects

let plotLineXY xvalues (yvalues: _ list) =
    Chart.Line(xvalues, yvalues)
    |> Chart.withSize(800.0, 300.0)
    |> Chart.withMargin(Margin.init(5,5,15,5))

let plotLine (yvalues: _ list) =
    let xvalues = List.init (yvalues |> List.length) float
    plotLineXY xvalues yvalues 

let plotVide sampleRate durationInSeconds (gen: Vide<_,_,_>) =
    let yvalues =
        gen 
        |> Gen.Eval.toSeq sampleRate
        |> Seq.take (sampleRate * durationInSeconds |> int)
        |> Seq.toList
    let xvalues = List.init yvalues.Length (fun y -> float y / sampleRate)
    plotLineXY xvalues yvalues
    
let plotVides sampleRate durationInSeconds gens =
    gens
    |> List.map (plotVide sampleRate durationInSeconds)
    |> Chart.combine

let plotVide44k durationInSeconds gen = plotVide 44100.0 durationInSeconds gen
    
let plotVides44k durationInSeconds gens = plotVides 44100.0 durationInSeconds gens

In [3]:
// modulate a sine wave with another sine wave
let modulatedSignal = dsp {
    let! sin1 = Gen.Osc.sin 30.0
    let! sin2 = Gen.Osc.sin 7.0
    return sin1 * sin2
}

modulatedSignal |> plotVide44k 1.0

<!-- Plotly chart will be drawn inside this DIV -->

In [4]:
// apply some noise to the modulates signal
let noisyModulated = dsp {
    let! modulated = modulatedSignal
    let! noise = Gen.Osc.noise
    return modulated * noise
}

noisyModulated |> plotVide44k 1.0

<!-- Plotly chart will be drawn inside this DIV -->

In [5]:
[
    noisyModulated |> plotVide44k 1.0
    (
        noisyModulated
        |=> Fx.Filter.lowPass { frq = 50.0; q = 0.9; gain = 1.0 }
        |> plotVide44k 1.0
    )
]
|> Chart.combine


<!-- Plotly chart will be drawn inside this DIV -->